Creating the dataset subset with FiftyOne


In [16]:
import fiftyone as fo
import fiftyone.zoo as foz

import json
import cv2
import os
import matplotlib.pyplot as plt
import shutil

In [ ]:


# # Load a COCO dataset subset with vehicle annotations

# dataset = foz.load_zoo_dataset(
#     "coco-2017",
#     split="train",
#     max_samples=5000,  # Adjust number of samples as needed
#     classes=["car"=3, "bus"=6, "truck"=8, "motorcycle"=4],  # Target objects
#     label_types=["detections"]
# )


# # Visualize the dataset
# session = fo.launch_app(dataset)


In [15]:
print(fo.list_datasets())
dataset = fo.load_dataset("coco-2017-train-5000")
session = fo.launch_app(dataset)


['coco-2017', 'coco-2017-5000', 'coco-2017-train-5000', 'coco-2017-validation-100', 'coco-2017-validation-20']


Now we should convert from coco format to match the yolo format

Setting Paths and Reading JSON Annotation file


The input path is the path of the dataset that we want to convert into the YOLO format.
Output path is the path where a new converted dataset will be saved.


In [32]:

coco_annotations_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/labels.json'
input_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/data'
output_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/'
f = open(coco_annotations_path)
data = json.load(f)
f.close()

Processing Images



In [38]:
file_names = []

def load_images_from_folder(folder):
    count = 0
    images_output_path = os.path.join(output_path, "images")
    
    # Ensure the output directories exist
    os.makedirs(images_output_path, exist_ok=True)
    
    for filename in os.listdir(folder):
        source = os.path.join(folder, filename)
        destination = os.path.join(images_output_path, f"img{count}.jpg")

        try:
            shutil.copy(source, destination)
            print(f"File {filename} copied successfully as img{count}.jpg")
        except shutil.SameFileError:
            print("Source and destination represents the same file.")

        # Append the original filename (not the new one) if needed for later reference
        file_names.append(filename)
        count += 1

load_images_from_folder(input_path)

File 000000000064.jpg copied successfully as img0.jpg
File 000000000071.jpg copied successfully as img1.jpg
File 000000000073.jpg copied successfully as img2.jpg
File 000000000086.jpg copied successfully as img3.jpg
File 000000000094.jpg copied successfully as img4.jpg
File 000000000149.jpg copied successfully as img5.jpg
File 000000000247.jpg copied successfully as img6.jpg
File 000000000257.jpg copied successfully as img7.jpg
File 000000000260.jpg copied successfully as img8.jpg
File 000000000307.jpg copied successfully as img9.jpg
File 000000000328.jpg copied successfully as img10.jpg
File 000000000359.jpg copied successfully as img11.jpg
File 000000000419.jpg copied successfully as img12.jpg
File 000000000471.jpg copied successfully as img13.jpg
File 000000000529.jpg copied successfully as img14.jpg
File 000000000532.jpg copied successfully as img15.jpg
File 000000000540.jpg copied successfully as img16.jpg
File 000000000629.jpg copied successfully as img17.jpg
File 000000000641.jp

Helper Functions


This function takes an image_id as a parameter and returns the annotations of that image.


In [25]:
def get_img_ann(image_id):
    img_ann = []
    isFound = False
    for ann in data['annotations']:
        if ann['image_id'] == image_id:
            img_ann.append(ann)
            isFound = True
    if isFound:
        return img_ann
    else:
        return None

To get the relative annotations for an image, I have created a helper function and its implementation details are given below:



In [26]:

# Create an empty list to store the image annotations: img_ann
# Using a for loop to traverse through all the annotations in the data.
# Uses an if condition to check for the required image_id .
# If image id matches, append the annotations for this image into the list we have created i.e: img_ann
# I am using an isFound as a flag to check whether an image’s annotations are found or not. In case of not found, I am returning a None.

def get_img(filename):
  for img in data['images']:
    if img['file_name'] == filename:
      return img

In the function I mentioned above get_img() I want to extract the relative image information such as 'id' , 'height' and 'width' by matching image filenames. If the filename matches, it returns image information in the form of a dictionary.

Processing Labels

In [ ]:
# Applying Conversion.
# Following are the steps we are going to perform in conversion:

# Extracting image information such as image_id, image_width, image_height, etc.
# Get annotations for this image using image_id.
# Open a text file for this image in the output path given by the user.
# Extract bounding box properties for each object in the image.
# Finding midpoint coordinates.
# Apply Normalization.
# Setting precision.
# Writing the updated annotations for this image into a text file.
# After processing through all the annotations for the current image, close the text file.
# Repeat the steps for all images.

In [37]:
# COCO category IDs to our custom class IDs
coco_to_custom = {3: 0, 6: 1, 8: 2, 4: 3}  # car, bus, truck, motorcycle


count = 0
for filename in file_names:
    img = get_img(filename)
    if img is None:
        continue
    # Make sure the output directory for labels exists
    labels_output_path = os.path.join(output_path, "labels")
    os.makedirs(labels_output_path, exist_ok=True)  # This creates the directory if it does not exist
    img_id = img['id']
    img_w = img['width']
    img_h = img['height']
    
    img_ann = get_img_ann(img_id)
    if img_ann:
        print(f"Annotations found for image ID {img_id}: {len(img_ann)}")

    # File path for YOLO labels
    file_path = os.path.join(labels_output_path, f"img{count}.txt")
    
    with open(file_path, "w") as file_object:
        for ann in img_ann:
            # Default to "other" class (4) if not in our specific categories
            current_category = coco_to_custom.get(ann['category_id'], 4)  # Use `get` with default value
            
            # COCO format: [x_min, y_min, width, height]
            x, y, w, h = ann['bbox']
            
            # Convert to YOLO format: Normalize [x_center, y_center, width, height]
            x_center = (x + w / 2) / img_w
            y_center = (y + h / 2) / img_h
            w_norm = w / img_w
            h_norm = h / img_h

            # Write to file: YOLO format
            file_object.write(f"{current_category} {x_center:.6f} {y_center:.6f} {w_norm:.6f} {h_norm:.6f}\n")

            print(f"Writing to {file_path}: {current_category} {x_center:.6f} {y_center:.6f} {w_norm:.6f} {h_norm:.6f}")

    count += 1  # Move to next image/file


Annotations found for image ID 64: 4
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img0.txt: 0 0.292792 0.729031 0.367417 0.246281
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img0.txt: 2 0.239438 0.599242 0.259542 0.092922
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img0.txt: 4 0.279896 0.412773 0.077125 0.117453
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img0.txt: 4 0.394146 0.184914 0.321458 0.237984
Annotations found for image ID 71: 16
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img1.txt: 0 0.752648 0.525833 0.043359 0.033216
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/train/yolo_labels/labels\img1.txt: 0 0.835727 0.538498 0.038047 0.028169
Writing to C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-20

Now we will do the same proccess for the validation set

In [39]:


# Load validation annotations
val_coco_annotations_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/validation/labels.json'
val_input_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/validation/data'
val_output_path = 'C:/Users/Adi/Desktop/fourthyear/DL-Proj/datasets/coco-2017/validation/yolo_labels/'

with open(val_coco_annotations_path) as f:
    val_data = json.load(f)

val_file_names = []

# Function to load images from validation folder and copy them with new naming convention
def load_images_from_folder(folder, output_path):
    count = 0
    images_output_path = os.path.join(output_path, "images")
    
    # Ensure the output directories exist
    os.makedirs(images_output_path, exist_ok=True)
    
    for filename in os.listdir(folder):
        source = os.path.join(folder, filename)
        destination = os.path.join(images_output_path, f"img{count}.jpg")

        try:
            shutil.copy(source, destination)
            print(f"File {filename} copied successfully as img{count}.jpg")
        except shutil.SameFileError:
            print("Source and destination represent the same file.")

        val_file_names.append(filename)
        count += 1

load_images_from_folder(val_input_path, val_output_path)

# COCO category IDs to our custom class IDs (same as for the training dataset)
coco_to_custom = {3: 0, 6: 1, 8: 2, 4: 3}  # car, bus, truck, motorcycle

# Adjust the get_img and get_img_ann functions for validation data
def get_val_img(filename):
    for img in val_data['images']:
        if img['file_name'] == filename:
            return img

def get_val_img_ann(image_id):
    img_ann = [ann for ann in val_data['annotations'] if ann['image_id'] == image_id]
    return img_ann

# Process validation annotations in YOLO format
count = 0
for filename in val_file_names:
    img = get_val_img(filename)
    if img is None:
        continue

    labels_output_path = os.path.join(val_output_path, "labels")
    os.makedirs(labels_output_path, exist_ok=True)

    img_id = img['id']
    img_w = img['width']
    img_h = img['height']
    
    img_ann = get_val_img_ann(img_id)
    if img_ann:
        print(f"Annotations found for image ID {img_id}: {len(img_ann)}")

    file_path = os.path.join(labels_output_path, f"img{count}.txt")
    
    with open(file_path, "w") as file_object:
        for ann in img_ann:
            current_category = coco_to_custom.get(ann['category_id'], 4)  # Default to "other"
            
            x, y, w, h = ann['bbox']
            x_center = (x + w / 2) / img_w
            y_center = (y + h / 2) / img_h
            w_norm = w / img_w
            h_norm = h / img_h

            file_object.write(f"{current_category} {x_center:.6f} {y_center:.6f} {w_norm:.6f} {h_norm:.6f}\n")
            print(f"Writing to {file_path}: {current_category} {x_center:.6f} {y_center:.6f} {w_norm:.6f} {h_norm:.6f}")

    count += 1


File 000000000724.jpg copied successfully as img0.jpg
File 000000001532.jpg copied successfully as img1.jpg
File 000000001584.jpg copied successfully as img2.jpg
File 000000002006.jpg copied successfully as img3.jpg
File 000000005001.jpg copied successfully as img4.jpg
File 000000005037.jpg copied successfully as img5.jpg
File 000000006040.jpg copied successfully as img6.jpg
File 000000006723.jpg copied successfully as img7.jpg
File 000000007088.jpg copied successfully as img8.jpg
File 000000007386.jpg copied successfully as img9.jpg
File 000000007816.jpg copied successfully as img10.jpg
File 000000008211.jpg copied successfully as img11.jpg
File 000000008762.jpg copied successfully as img12.jpg
File 000000008899.jpg copied successfully as img13.jpg
File 000000009769.jpg copied successfully as img14.jpg
File 000000009891.jpg copied successfully as img15.jpg
File 000000010363.jpg copied successfully as img16.jpg
File 000000011149.jpg copied successfully as img17.jpg
File 000000011197.jp

now that we have our images and YOLO-formatted label files ready, we're set to prepare for and start training with YOLO. focusing on YOLOv5